CTGAN Runner (SDV-based)

This script trains a CTGAN model on single-cell (tabular) data using the SDV library
(and falls back to the standalone 'ctgan' package if needed). It supports three study
scenarios used in the paper:

1) PBMC3K:
   - Trains CTGAN on real train samples with 100epc.
   - Generates synthetic samples equal to TEST sample size.
   - Saves: pbmc3k_CTGAN_100epc.pkl

2) HCA-BM10K (5-fold CV)
3) Integrated Pancreatic dataset (5-fold CV)
   - For EACH FOLD:
       * Fit CTGAN on TRAIN ONLY.
       * Generate synthetic samples to reach the number of corresponding Q3 value of cell-type distribution.
         (per-class if --label-col is provided; labels are assigned accordingly).
       * Augment TRAIN with synthetic. VALIDATION/TEST are NEVER touched.
       * Saves per-fold files under: {output}/folds/fold_{i}/
         - dictionary includes each fold: train_gen, y_train_gen

In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


In [ ]:
import torch
print(torch.__version__)
print("GPU available:", torch.cuda.is_available())

2.6.0+cu124
GPU available: True


In [ ]:
pip install sdv --quiet

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 185.6/185.6 kB 10.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 140.1/140.1 kB 14.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.0/14.0 MB 120.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 52.7/52.7 kB 5.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.8/73.8 kB 8.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 198.1/198.1 kB 18.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.9/1.9 MB 56.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.3/85.3 kB 8.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 3.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 126.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 102.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 59.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6

In [ ]:
import sdv
import os
import time
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt


In [ ]:
import sdv
print(sdv.__version__)

1.25.0


In [ ]:
from sdv.single_table import GaussianCopulaSynthesizer
from sdv.single_table import CTGANSynthesizer
from sdv.single_table import TVAESynthesizer
from sdv.single_table import CopulaGANSynthesizer

from sdv.metadata import Metadata

Pbmc3k

In [ ]:
import pickle
with open(f"data/pbmc3k_train.pkl", "rb") as f:
    X_train = pickle.load(f)
with open(f"data/pbmc3k_test.pkl", "rb") as f:
    X_test = pickle.load(f)
with open(f"data/pbmc3k_y_train.pkl", "rb") as f:
    y_train = pickle.load(f)
with open(f"data/pbmc3k_y_test.pkl", "rb") as f:
    y_test = pickle.load(f)

Pancrea 5CV

In [ ]:
import pickle

all_folds = []

for fold in range(1, 6):
    with open(f"/data/5CV/fold_skf_3000_{fold}.pkl", "rb") as f:
        fold_data = pickle.load(f)
        all_folds.append(fold_data)


In [ ]:
for i,f in enumerate(all_folds, start=1):
  print(f"Fold {i}:")
  print("X_train shape:", f['X_train'].shape)
  print("y_train shape:", f['y_train'].shape)

Fold 1:
X_train shape: (11337, 3000)
y_train shape: (11337,)
Fold 2:
X_train shape: (11337, 3000)
y_train shape: (11337,)
Fold 3:
X_train shape: (11338, 3000)
y_train shape: (11338,)
Fold 4:
X_train shape: (11338, 3000)
y_train shape: (11338,)
Fold 5:
X_train shape: (11338, 3000)
y_train shape: (11338,)


In [ ]:
unique_values, counts = np.unique(all_folds[0]['y_train'], return_counts=True)
display(dict(zip(unique_values, counts)),np.max(counts))

HCA

In [ ]:
import pickle

all_folds = []

for fold in range(1, 6):
    with open(f"HCA/5CV/fold_skf_{fold}.pkl", "rb") as f:
        fold_data = pickle.load(f)
        all_folds.append(fold_data)


In [ ]:
X_train = all_folds[0]['X_train']
X_test = all_folds[0]['X_test']
y_train = all_folds[0]['y_train']
y_test = all_folds[0]['y_test']

In [ ]:
X_train.shape, X_test.shape, y_train.shape, y_test.shape

((8000, 3000), (2000, 3000), (8000,), (2000,))

CTGAN

In [ ]:
import torch
def generate_ctgan(metadata,num_synthetic_samples, X_min):
    ctgan = CTGANSynthesizer(metadata,epochs=100,verbose=True)
    ctgan.fit(X_min)
    ctgan_synthetic = ctgan.sample(num_synthetic_samples)

    return ctgan_synthetic

PBMC3k

In [ ]:
metadata = Metadata()
metadata = metadata.detect_from_dataframe(X_train)
numeric_cols = list(X_train.columns)
for col in numeric_cols:
  metadata.update_column(
  column_name=col,
  sdtype='numerical'
  )
synthetic_samples = generate_ctgan(metadata, int(X_test.shape[0]),X_train )

/usr/local/lib/python3.11/dist-packages/sdv/single_table/base.py:129: UserWarning: We strongly recommend saving the metadata using 'save_to_json' for replicability in future SDV versions.
  warnings.warn(


PerformanceAlert: Using the CTGANSynthesizer on this data is not recommended. To model this data, CTGAN will generate a large number of columns.

Original Column Name   Est # of Columns (CTGAN)
PPBP                   11
LYZ                    11
S100A9                 11
IGLL5                  11
GNLY                   11
FTL                    11
PF4                    11
FTH1                   11
GNG11                  11
S100A8                 11
FCER1A                 11
HLA-DRA                11
CD74                   11
CLU                    11
NKG7                   11
GZMB                   11
CST3                   11
CCL4                   11
C1QA                   11
HLA-DPB1               11
SDPR                   11
C1QB                   11
AL928768.3             11
TUBB1                  11
GUSB                   11
C10orf32               11
GP9                    11
LYPD2                  11
LYAR                   11
HAGH                   11
FUS                    11


Gen. (1.28) | Discrim. (-1.25): 100%|██████████| 100/100 [14:43<00:00,  8.83s/it]


In [ ]:
synthetic_samples.shape

(264, 2000)

In [ ]:
with open("results" + os.sep + f'pbmc3k_CTGAN_100epc.pkl', 'wb') as f:
          pickle.dump(synthetic_samples, f)

5CV

In [ ]:
import contextlib
@contextlib.contextmanager
def suppress_output():
    with open(os.devnull, 'w') as devnull:
        old_stdout = sys.stdout
        sys.stdout = devnull
        try:
            yield
        finally:
            sys.stdout = old_stdout
def ctGAN_CV():
  gen_dict = []
  #for k, fold in enumerate(all_folds, start=1):
  for k, fold in enumerate(all_folds, start=1):
      X_train = fold['X_train']
      X_val = fold['X_val']
      y_train = fold['y_train']
      y_val = fold['y_val']

      metadata = Metadata()
      metadata = metadata.detect_from_dataframe(X_train)
      numeric_cols = list(X_train.columns)
      for col in numeric_cols:
          metadata.update_column(
              column_name=col,
              sdtype='numerical'
          )
      # Get unique values and their counts
      unique_values, counts = np.unique(y_train, return_counts=True)
      classlabel_counts = dict(zip(unique_values, counts))
      Q1, Q2, Q3 = np.quantile(counts, [0.25, 0.5, 0.75], axis=0, method='nearest')
      max_count = Q3 #np.max(counts)

      i=1
      for label, count in classlabel_counts.items():
          #print(x.shape, y.shape)
          print("label, count, max_count",label,count,max_count)
          X_minority = X_train[y_train == label]
          if count < max_count:
              #print("\n")
              #print(f"Value {label} appears {count} times.")
              num_synthetic_samples = max_count - count
              synthetic_samples = generate_ctgan(metadata, num_synthetic_samples, X_minority)

              X_minority = np.array(X_minority)
              synthetic_samples = np.array(synthetic_samples)
              if i==1:
                X_train_gen = X_minority
                X_train_gen = np.vstack([X_train_gen, synthetic_samples])

                y_train_gen = np.full(max_count, label)

                y_train_indexes = np.full(count, 1)
                y_train_indexes = np.concatenate([y_train_indexes, np.full(num_synthetic_samples, 2)])
              else:
                tmp = np.vstack([X_minority, synthetic_samples])
                X_train_gen = np.vstack([X_train_gen, tmp])
                y_train_gen = np.concatenate([y_train_gen, np.full(max_count, label)])

                y_train_indexes = np.concatenate([y_train_indexes, np.full(count, 1)])
                y_train_indexes = np.concatenate([y_train_indexes, np.full(num_synthetic_samples, 2)])
          else:
              X_train_gen = np.vstack([X_train_gen, X_minority])
              y_train_gen = np.concatenate([y_train_gen, np.full(count, label)])
              y_train_indexes = np.concatenate([y_train_indexes, np.full(count, 1)])
          i=i+1

      syn = {
          'X_train_gen': X_train_gen,
          'y_train_gen': y_train_gen
      }
      gen_dict.append(syn)

      with open("HCA/5CV" + os.sep + f'ctGAN_skf_fold_'+str(k)+'.pkl', 'wb') as f:
          pickle.dump(syn, f)
      print(f"CTGAN results for fold {k} saved.")

  return gen_dict


In [ ]:
gen_dict = ctGAN_CV()

label, count, max_count 1 476 670


/usr/local/lib/python3.11/dist-packages/sdv/single_table/base.py:133: UserWarning: We strongly recommend saving the metadata using 'save_to_json' for replicability in future SDV versions.
  warnings.warn(


PerformanceAlert: Using the CTGANSynthesizer on this data is not recommended. To model this data, CTGAN will generate a large number of columns.

Original Column Name      Est # of Columns (CTGAN)
S100A9                    11
S100A8                    11
LYZ                       11
CD74                      11
HLA-DRA                   11
HBB                       11
MALAT1                    11
S100A4                    11
GNLY                      11
IGKC                      11
FTL                       11
NKG7                      11
S100A6                    11
CCL5                      11
TMSB4X                    11
TYROBP                    11
LGALS1                    11
FTH1                      11
CST3                      11
SRGN                      11
ACTB                      11
B2M                       11
HBA1                      11
FOS                       11
S100A12                   11
IGLC2                     11
MT-CO1                    11
HBA2                

Gen. (-8.02) | Discrim. (-1.05): 100%|██████████| 100/100 [06:56<00:00,  4.16s/it]


label, count, max_count 2 399 670
PerformanceAlert: Using the CTGANSynthesizer on this data is not recommended. To model this data, CTGAN will generate a large number of columns.

Original Column Name      Est # of Columns (CTGAN)
S100A9                    11
S100A8                    11
LYZ                       11
CD74                      11
HLA-DRA                   11
HBB                       11
MALAT1                    11
S100A4                    11
GNLY                      11
IGKC                      11
FTL                       11
NKG7                      11
S100A6                    11
CCL5                      11
TMSB4X                    11
TYROBP                    11
LGALS1                    11
FTH1                      11
CST3                      11
SRGN                      11
ACTB                      11
B2M                       11
HBA1                      11
FOS                       11
S100A12                   11
IGLC2                     11
MT-CO1         

...

label, count, max_count 16 58 670
PerformanceAlert: Using the CTGANSynthesizer on this data is not recommended. To model this data, CTGAN will generate a large number of columns.

Original Column Name      Est # of Columns (CTGAN)
S100A9                    11
S100A8                    11
LYZ                       11
CD74                      11
HLA-DRA                   11
HBB                       11
MALAT1                    11
S100A4                    11
GNLY                      11
IGKC                      11
FTL                       11
NKG7                      11
S100A6                    11
CCL5                      11
TMSB4X                    11
TYROBP                    11
LGALS1                    11
FTH1                      11
CST3                      11
SRGN                      11
ACTB                      11
B2M                       11
HBA1                      11
FOS                       11
S100A12                   11
IGLC2                     11
MT-CO1         

Gen. (-32.13) | Discrim. (12.55): 100%|██████████| 100/100 [05:28<00:00,  3.29s/it]


CTGAN results for fold 4 saved.
label, count, max_count 1 476 670


/usr/local/lib/python3.11/dist-packages/sdv/single_table/base.py:133: UserWarning: We strongly recommend saving the metadata using 'save_to_json' for replicability in future SDV versions.
  warnings.warn(


PerformanceAlert: Using the CTGANSynthesizer on this data is not recommended. To model this data, CTGAN will generate a large number of columns.

Original Column Name      Est # of Columns (CTGAN)
S100A9                    11
S100A8                    11
LYZ                       11
CD74                      11
HLA-DRA                   11
HBB                       11
MALAT1                    11
S100A4                    11
GNLY                      11
IGKC                      11
FTL                       11
NKG7                      11
S100A6                    11
CCL5                      11
TMSB4X                    11
TYROBP                    11
LGALS1                    11
FTH1                      11
CST3                      11
SRGN                      11
ACTB                      11
B2M                       11
HBA1                      11
FOS                       11
S100A12                   11
IGLC2                     11
MT-CO1                    11
HBA2                